The following cell sets the input values required to run the the optimisation model ``..\MINIZINC\hydrogen_plant.mzn``.

This input data are stored in ``..\MINIZINC\hydrogen_plant_data.dzn``. This input file preparation is carried out by ``make_dzn_file`` function that is in ``..\PYTHON\PACKAGE\optimisation.py``.

Then the minizinc optimisation is executed by ``optimise()`` function that is in ``..\PYTHON\PACKAGE\optimisation.py``. 

``projdirs`` stores the key paths for the entire package.

In [41]:
import pandas as pd
import numpy as np
import os
from projdirs import datadir #load the path that contains the data files 
from PACKAGE.optimisation import make_dzn_file, optimise


#Load the weather data file and extract wind speed and solar irradiance from it
DATA = pd.read_csv(datadir + r'TEST DATA\SAM_60min\086282TMY_60min_SAM.csv',skiprows=2)
solar = DATA['global horizontal irradiance'][0:1000].copy().tolist()
wind = DATA['wind speed'][0:1000].copy().tolist()

# create a dictionary that contains the inputs for optimisation.
#these inputs are used by make_dzn_file function to create an input text file called hydrogen_plant_data.dzn. 
simparams = dict(DT = 3600,#[s] time steps
                 ETA_EL = 0.80,       #efficiency of electrolyser
                 BAT_ETA_in = 0.95,   #charging efficiency of battery
                 BAT_ETA_out = 0.95,  #discharg efficiency of battery
                 C_PV = 2,          #[$/W] unit cost of PV
                 C_W = 1.6,           #[$/W] unit cost of W
                 C_EL = 0.5,          #[$/W] unit cost of electrolyser
                 C_HS = 16,           #[$/kgH] unit cost of hydrogen storage
                 C_BAT = 50/1000/3600,        #[$/W.s] unit cost of battery storage
                 CF = 0.99,           #capacity factor
                 S = solar,           #[W/m2] solar irradiance time series
                 W = wind,            #wind speed timeseries
                 L = [0.1 for i in range(len(solar))])       #[kgH/s] load profile timeseries

#run the optimisation function and get the results in a dictionary:
results = optimise(simparams)


print (
        'CAPEX = %0.2f [M$]' %( results['CAPEX'][0]/1e6 ),'\n'
        'pv_max = %0.2f [MW]' %( results['pv_max'][0]/1e6 ),'\n'  
        'w_max = %0.2f [MW]' %( results['w_max'][0]/1e6 ),'\n'    
        'el_max = %0.4f [MW]' %( results['el_max'][0]/1e6 ),'\n'  
        'hs_max = %0.2f [T of H2]' %( results['hs_max'][0]/1e3 ),'\n'  
        'bat_capa = %0.2f [MWh]' %( results['bat_capa'][0]/3.6e9  ),'\n'  
        'bat_pmax = %0.2f [MW]' %( results['bat_pmax'][0]/1e6 )
        )


#transfer the data from 'results' to a dataframe for plotting: 
data_plot = pd.DataFrame(dict(t= np.arange(0,len(simparams['S'])),
                              solar=simparams['S'], wind=simparams['W'],
                              pv_out=results['pv_out'],
                              w_out=results['w_out'],
                              pc=results['pc'],
                              he_out = results['he_out'],
                              hr_out = results['hr_out'],
                              sh = results['sh'][0:-1],
                              R = results['r'][0:-1],
                              L = results['L'],
                              hs_out = results['L']-results['hr_out'],
                              bat_e_stored = results['bat_e_stored'][0:-1],
                              bat_pin = results['bat_pin'],
                              bat_pout = results['bat_pout']
                             ))

#create a new column for datetime for plotting. This column is timestamped from the 
#beginning of 2022
data_plot['time'] =pd.to_datetime('2022-01-01') + pd.to_timedelta(data_plot.t, 'h')
data_plot.drop('t',axis=1,inplace=True)



CAPEX = 256.34 [M$] 
pv_max = 46.33 [MW] 
w_max = 88.25 [MW] 
el_max = 41.8412 [MW] 
hs_max = 13.55 [T of H2] 
bat_capa = 26.63 [MWh] 
bat_pmax = 28.03 [MW]


In [45]:
data_plot[(data_plot.wind>3) & (data_plot.wind<13) ]

solar    wind        pv_out         w_out            pc    he_out  \
0      0.638560  4.0969  2.958520e+04  1.061805e+06  0.000000e+00  0.006149   
1      0.455680  3.9578  2.111217e+04  8.095814e+05  0.000000e+00  0.004680   
2      0.272800  3.8186  1.263913e+04  5.913633e+05  0.000000e+00  0.003403   
3      0.089916  3.6794  4.165910e+03  4.073446e+05  0.000000e+00  0.002318   
4      0.905500  4.4119  4.195283e+04  1.759214e+06  0.000000e+00  0.010147   
..          ...     ...           ...           ...           ...       ...   
995  826.510000  6.2964  3.829314e+07  9.589384e+06  4.788252e+07  0.000000   
996  743.440000  6.3750  3.444441e+07  1.005214e+07  2.655353e+06  0.235725   
997  710.950000  5.1944  3.293911e+07  4.249545e+06  2.071225e+07  0.092825   
998  728.680000  8.2686  3.376056e+07  2.449635e+07  5.825691e+07  0.000000   
999  656.620000  6.8519  3.042194e+07  1.309365e+07  4.351560e+07  0.000000   

       hr_out          sh            R    L    hs_out  bat_e_stored  bat_pin  \
0    0.088296   20.000000  3600.000000  0.1  0.011704          -0.0      0.0   
1    0.095320    0.000000  3282.135247  0.1  0.004680          -0.0      0.0   
2    0.096597    0.000000  2938.983118  0.1  0.003403          -0.0      0.0   
3    0.097682    0.000000  2591.233308  0.1  0.002318          -0.0      0.0   
4    0.089853    0.000000  2239.579437  0.1  0.010147          -0.0      0.0   
..        ...         ...          ...  ...       ...           ...      ...   
995  0.000000  617.220401     0.000000  0.1  0.100000           0.0      0.0   
996  0.000000  257.220401     0.000000  0.1  0.100000           0.0      0.0   
997  0.000000  745.830601     0.000000  0.1  0.100000           0.0      0.0   
998  0.000000  720.000000     0.000000  0.1  0.100000           0.0      0.0   
999  0.000000  360.000000     0.000000  0.1  0.100000           0.0      0.0   

     bat_pout                time  
0         0.0 2022-01-01 00:00:00  
1         0.0 2022-01-01 01:00:00  
2         0.0 2022-01-01 02:00:00  
3         0.0 2022-01-01 03:00:00  
4         0.0 2022-01-01 04:00:00  
..        ...                 ...  
995       0.0 2022-02-11 11:00:00  
996       0.0 2022-02-11 12:00:00  
997       0.0 2022-02-11 13:00:00  
998       0.0 2022-02-11 14:00:00  
999       0.0 2022-02-11 15:00:00  

[822 rows x 15 columns]

In [42]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
#               line_shape='hv', name='Solar Irrad.'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )
# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.sh),
              name='Stored H',yaxis="y1"),
                )


fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.R),
              name='R',yaxis="y1")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.he_out),
              line_shape='hv',name='he_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hs_out),
              line_shape='hv',name='hs_out',yaxis="y2")
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.hr_out),
              line_shape='hv',name='hr_out',yaxis="y2")
                )



fig.update_layout(
    yaxis1=dict(
        range=[0, max(data_plot.sh)]
    ),
    yaxis2=dict(
        range=[0, 0.4]
    )
    
)
    

fig.show()

In [30]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
# fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
              line_shape='hv', name='Solar Irrad.', yaxis="y2"),
                )

# fig.add_trace(
#     go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
#               line_shape='hv', name='Wind Speed'),
#                 )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pv_out),
              line_shape='hv', name='pv_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.w_out),
              line_shape='hv', name='w_out'),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.pc),
              line_shape='hv', name='pc'),
                )




# fig.update_layout(
#     yaxis1=dict(
#         range=[0, 15000]
#     ),
#     yaxis2=dict(
#         range=[0, 0.4]
#     )
    
# )
    

fig.show()


In [31]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.solar),
              line_shape='hv', name='Solar Irrad.', yaxis="y1"),
                )

fig.add_trace(
    go.Scatter(x=list(data_plot.time), y=list(data_plot.wind),
              line_shape='hv', name='Wind Speed', yaxis="y2"),
                )



# fig.update_layout(
#     yaxis1=dict(
#         range=[0, 15000]
#     ),
#     yaxis2=dict(
#         range=[0, 0.4]
#     )
    
# )
    

fig.show()
